# MOSAiC campaign in FOCI NEMO Test data

_**--- work in progress ---**_

## Description

We use an [Intake driver](https://github.com/ESM-VFC/intake_pangaeapy) for [`pangaeapy`](https://github.com/pangaea-data-publisher/pangaeapy) to load the master track of the Polarstern cruise PS122/1 (MOSAiC leg 1) and plot the data together with ice-coverage information from the FOCI NEMO test dataset.

_**Note** that we cannot expect a lot of similarity between the in-sity observational data and a free running climate model data that we use for testing here._

## Caveats

- We don't have test data covering the real MOSAiC cruise dates yet.
- The test data we use here are from a free running intermediate-resolution climate model development run. So we cannot expect the ice conditions in the virtual campaign to represent the realistic contitions.
- ...

## Design goals

We aim at boiling down the user interaction to only the following steps:
- pick a field campaign (Here: "PS122_1_master_track" from the MOSAiC Catalog)
- pick a model experiment (Here: "FOCI Minimal Test Dataset") and a set of variables (Here: "Ice characteristics")
- pick plots of interest (Here: "Speed, Course, Position for PS122/1" and "Ice thickness for FOCI test run")

The results should be:
- the plots shown below
- a tabular dataset with the model data sampled where the field campaign was sampling

## Parameters

In [1]:
# parameters

esm_vfc_data_dir = "../esm-vfc-data/"
nemo_catalog_url = "https://raw.githubusercontent.com/ESM-VFC/esm-vfc-catalogs/master/catalogs/NEMO_ORCA05_FOCI_Test_Minimal.yaml"
mosaic_catalog_url = "https://raw.githubusercontent.com/ESM-VFC/esm-vfc-catalogs/master/catalogs/MOSAIC.yaml"
dask_cluster_args = dict(
    n_workers=1, threads_per_worker=2, memory_limit=4e9,
    host="127.0.0.1")

## Tech preamble

In [2]:
import numpy as np
import pandas as pd
import xarray as xr

In [3]:
# set up intake catalog
import intake
from esmvfc_cattools import fetch_zenodo_data
import os

os.environ["ESM_VFC_DATA_DIR"] = esm_vfc_data_dir

In [4]:
# set up plotting
import hvplot.pandas
import hvplot.xarray
import geoviews.feature as gf
import geoviews as gv
from holoviews.operation import decimate
from cartopy import crs

In [5]:
import xorca_lonlat2ij as xll2ij

In [6]:
# set up Dask cluster
from dask.distributed import Client
client = Client(**dask_cluster_args)
client

<Client: 'tcp://127.0.0.1:35693' processes=1 threads=2, memory=2.09 GB>

## Get MOSAiC track via the catalog

In [7]:
mosaic_catalog = intake.open_catalog(mosaic_catalog_url)
list(mosaic_catalog)

['PS122_1_master_track']

In [8]:
print(mosaic_catalog["PS122_1_master_track"].description)

Rex, Markus (2020): Links to master tracks in different resolutions of
POLARSTERN cruise PS122/1, Tromsø - Arctic Ocean, 2019-09-20 - 2019-12-13.
Alfred Wegener Institute, Helmholtz Centre for Polar and Marine Research,
Bremerhaven, PANGAEA, https://doi.org/10.1594/PANGAEA.911224



In [9]:
mosaic_track = mosaic_catalog["PS122_1_master_track"].read()
mosaic_track = mosaic_track.set_index("Date/Time")

In [10]:
display(mosaic_track)

Latitude  Longitude  Speed  Course          Event
Date/Time                                                             
2019-09-20 17:50:00  69.67955   18.99664  0.001   226.2  PS122/1-track
2019-09-20 18:00:00  69.67955   18.99664  0.001    13.0  PS122/1-track
2019-09-20 18:10:00  69.67955   18.99664  0.000    90.0  PS122/1-track
2019-09-20 18:20:00  69.67955   18.99665  0.001    90.0  PS122/1-track
2019-09-20 18:30:00  69.67955   18.99664  0.001   270.0  PS122/1-track
...                       ...        ...    ...     ...            ...
2019-12-13 08:25:00  86.59291  119.27105  0.162   278.7  PS122/1-track
2019-12-13 08:35:00  86.59297  119.26354  0.162   278.0  PS122/1-track
2019-12-13 08:45:00  86.59304  119.25613  0.161   279.2  PS122/1-track
2019-12-13 08:55:00  86.59312  119.24856  0.164   280.2  PS122/1-track
2019-12-13 09:04:00  86.59319  119.24150  0.158   279.3  PS122/1-track

[11919 rows x 5 columns]

## Short inspection of the MOSAiC track

In [11]:
(
    mosaic_track.hvplot.points(
        "Longitude", "Latitude", color="Speed", label="Position / Speed",
        geo=True, projection=crs.NorthPolarStereo(central_longitude=85)
    ) * gf.land * gf.coastline
    + mosaic_track["Speed"].hvplot.line()
    + mosaic_track["Course"].hvplot.line() 
).cols(1)

:Layout
   .Overlay.Position_over_Speed :Overlay
      .Points.Position_over_Speed :Points   [Longitude,Latitude]   (Speed)
      .Land.I                     :Feature   [Longitude,Latitude]
      .Coastline.I                :Feature   [Longitude,Latitude]
   .Curve.Speed                 :Curve   [Date/Time]   (Speed)
   .Curve.Course                :Curve   [Date/Time]   (Course)

## Load catalog and fetch data

In [12]:
model_data_cat = intake.open_catalog(nemo_catalog_url)
fetch_zenodo_data(
    model_data_cat["NEMO_ORCA05_FOCI_Test_Minimal_icemod"]
)
fetch_zenodo_data(
    model_data_cat["NEMO_ORCA05_FOCI_Test_Minimal_mesh_mask"]
)

No need to download ../esm-vfc-data/NEMO_ORCA05_FOCI_Test_Minimal/FOCI1.14-TEST.2020.04.1_1m_20110101_20111231_icemod.nc
No need to download ../esm-vfc-data/NEMO_ORCA05_FOCI_Test_Minimal/mesh_mask.nc


## Load icemodel outputs

In [13]:
# hydrographic data
model_dataset = model_data_cat["NEMO_ORCA05_FOCI_Test_Minimal_icemod"].to_dask()
model_dataset = model_dataset.set_coords(["nav_lat", "nav_lon"])
model_dataset["nav_lat"] = model_dataset["nav_lat"].squeeze()
model_dataset["nav_lon"] = model_dataset["nav_lon"].squeeze()
model_dataset = xr.decode_cf(model_dataset)

# Need the grid definitions
model_meshmask = model_data_cat["NEMO_ORCA05_FOCI_Test_Minimal_mesh_mask"].to_dask()
model_meshmask = model_meshmask.squeeze()
model_meshmask = xr.decode_cf(model_meshmask)

In [14]:
display(model_dataset)
display(f"{model_dataset.nbytes / 1e9} GB")

<xarray.Dataset>
Dimensions:               (axis_nbounds: 2, time_counter: 12, x: 722, y: 511)
Coordinates:
    nav_lat               (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    nav_lon               (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    time_centered         (time_counter) datetime64[ns] dask.array<chunksize=(12,), meta=np.ndarray>
  * time_counter          (time_counter) datetime64[ns] 2011-01-16T12:00:00 ... 2011-12-16T12:00:00
Dimensions without coordinates: axis_nbounds, x, y
Data variables:
    ice_pres              (time_counter, y, x) float32 dask.array<chunksize=(12, 511, 722), meta=np.ndarray>
    time_centered_bounds  (time_counter, axis_nbounds) datetime64[ns] dask.array<chunksize=(12, 2), meta=np.ndarray>
    time_counter_bounds   (time_counter, axis_nbounds) datetime64[ns] dask.array<chunksize=(12, 2), meta=np.ndarray>
    ileadfra              (time_counter, y, x) float32 dask.array<chunksize=(12, 511, 722), meta=np.ndarray>
    isnowthi              (time_counter, y, x) float32 dask.array<chunksize=(12, 511, 722), meta=np.ndarray>
    iicethic              (time_counter, y, x) float32 dask.array<chunksize=(12, 511, 722), meta=np.ndarray>
    iiceprod              (time_counter, y, x) float32 dask.array<chunksize=(12, 511, 722), meta=np.ndarray>
    iicetemp              (time_counter, y, x) float32 dask.array<chunksize=(12, 511, 722), meta=np.ndarray>
    ioceflxb              (time_counter, y, x) float32 dask.array<chunksize=(12, 511, 722), meta=np.ndarray>
    iicevelu              (time_counter, y, x) float32 dask.array<chunksize=(12, 511, 722), meta=np.ndarray>
    iicevelv              (time_counter, y, x) float32 dask.array<chunksize=(12, 511, 722), meta=np.ndarray>
    iicestru              (time_counter, y, x) float32 dask.array<chunksize=(12, 511, 722), meta=np.ndarray>
    iicestrv              (time_counter, y, x) float32 dask.array<chunksize=(12, 511, 722), meta=np.ndarray>
    iicesflx              (time_counter, y, x) float32 dask.array<chunksize=(12, 511, 722), meta=np.ndarray>
    iicenflx              (time_counter, y, x) float64 dask.array<chunksize=(12, 511, 722), meta=np.ndarray>
    isnowpre              (time_counter, y, x) float32 dask.array<chunksize=(12, 511, 722), meta=np.ndarray>
Attributes:
    name:         FOCI1.14-JH024_1m_20110101_20111231
    description:  ice variables
    title:        ice variables
    Conventions:  CF-1.5
    production:   An IPSL model
    timeStamp:    2019-Apr-17 18:02:10 CEST
    history:      Wed Apr 17 18:48:52 2019: ncks -7 -a -L 1 --cnk_dmn time,1 ...
    NCO:          4.4.8

'0.268590352 GB'

In [15]:
display(model_meshmask)
display(f"{model_meshmask.nbytes / 1e9} GB")

<xarray.Dataset>
Dimensions:       (x: 722, y: 511, z: 46)
Dimensions without coordinates: x, y, z
Data variables:
    nav_lon       (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    nav_lat       (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    nav_lev       (z) float32 dask.array<chunksize=(46,), meta=np.ndarray>
    time_counter  float64 dask.array<chunksize=(), meta=np.ndarray>
    tmask         (z, y, x) int8 dask.array<chunksize=(46, 511, 722), meta=np.ndarray>
    umask         (z, y, x) int8 dask.array<chunksize=(46, 511, 722), meta=np.ndarray>
    vmask         (z, y, x) int8 dask.array<chunksize=(46, 511, 722), meta=np.ndarray>
    fmask         (z, y, x) int8 dask.array<chunksize=(46, 511, 722), meta=np.ndarray>
    tmaskutil     (y, x) int8 dask.array<chunksize=(511, 722), meta=np.ndarray>
    umaskutil     (y, x) int8 dask.array<chunksize=(511, 722), meta=np.ndarray>
    vmaskutil     (y, x) int8 dask.array<chunksize=(511, 722), meta=np.ndarray>
    fmaskutil     (y, x) int8 dask.array<chunksize=(511, 722), meta=np.ndarray>
    glamt         (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    glamu         (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    glamv         (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    glamf         (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    gphit         (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    gphiu         (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    gphiv         (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    gphif         (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e1t           (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e1u           (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e1v           (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e1f           (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e2t           (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e2u           (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e2v           (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e2f           (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    ff            (y, x) float64 dask.array<chunksize=(511, 722), meta=np.ndarray>
    mbathy        (y, x) int16 dask.array<chunksize=(511, 722), meta=np.ndarray>
    misf          (y, x) int16 dask.array<chunksize=(511, 722), meta=np.ndarray>
    isfdraft      (y, x) float32 dask.array<chunksize=(511, 722), meta=np.ndarray>
    e3t_0         (z, y, x) float64 dask.array<chunksize=(46, 511, 722), meta=np.ndarray>
    e3u_0         (z, y, x) float64 dask.array<chunksize=(46, 511, 722), meta=np.ndarray>
    e3v_0         (z, y, x) float64 dask.array<chunksize=(46, 511, 722), meta=np.ndarray>
    e3w_0         (z, y, x) float64 dask.array<chunksize=(46, 511, 722), meta=np.ndarray>
    gdept_0       (z, y, x) float32 dask.array<chunksize=(46, 511, 722), meta=np.ndarray>
    gdepu         (z, y, x) float32 dask.array<chunksize=(46, 511, 722), meta=np.ndarray>
    gdepv         (z, y, x) float32 dask.array<chunksize=(46, 511, 722), meta=np.ndarray>
    gdepw_0       (z, y, x) float32 dask.array<chunksize=(46, 511, 722), meta=np.ndarray>
    gdept_1d      (z) float64 dask.array<chunksize=(46,), meta=np.ndarray>
    gdepw_1d      (z) float64 dask.array<chunksize=(46,), meta=np.ndarray>
    e3t_1d        (z) float64 dask.array<chunksize=(46,), meta=np.ndarray>
    e3w_1d        (z) float64 dask.array<chunksize=(46,), meta=np.ndarray>

'0.928259736 GB'

In [16]:
# northern hemisphere ice thickness
ice_thickness = model_dataset.iicethic.where(
    (model_dataset.nav_lat > 0) & (model_meshmask.tmaskutil > 0)
)
ice_thickness = ice_thickness.isel(y=slice(400, None))

In [17]:
ice_thickness

<xarray.DataArray 'iicethic' (time_counter: 12, y: 111, x: 722)>
dask.array<getitem, shape=(12, 111, 722), dtype=float32, chunksize=(12, 111, 722), chunktype=numpy.ndarray>
Coordinates:
    nav_lat        (y, x) float32 dask.array<chunksize=(111, 722), meta=np.ndarray>
    nav_lon        (y, x) float32 dask.array<chunksize=(111, 722), meta=np.ndarray>
    time_centered  (time_counter) datetime64[ns] dask.array<chunksize=(12,), meta=np.ndarray>
  * time_counter   (time_counter) datetime64[ns] 2011-01-16T12:00:00 ... 2011-12-16T12:00:00
Dimensions without coordinates: y, x
Attributes:
    standard_name:       sea_ice_thickness
    long_name:           Ice thickness (cell average)
    units:               m
    online_operation:    average
    interval_operation:  10800 s
    interval_write:      1 month
    cell_methods:        time: mean (interval: 10800 s)

## Plot regions of ice > 2.0m in October to December with PS122/1 track

In [18]:
import cartopy.feature as cf

In [19]:
graticules = cf.NaturalEarthFeature(
    category='physical',
    name='graticules_10',
    scale='110m',
    style=dict(linewidth=0.2)
)

In [20]:
(
    gv.Feature(graticules).options(line_width=0.3)
    * ice_thickness.isel(time_counter=9).hvplot.contourf(
        alpha=0.15, levels=[2.0, 100],
        geo=True, projection=crs.NorthPolarStereo(central_longitude=0),
        colorbar=False
    )
    * ice_thickness.isel(time_counter=10).hvplot.contourf(
        alpha=0.15, levels=[2.0, 100],
        geo=True, projection=crs.NorthPolarStereo(central_longitude=0),
        colorbar=False
    )
    * ice_thickness.isel(time_counter=11).hvplot.contourf(
        alpha=0.15, levels=[2.0, 100],
        geo=True, projection=crs.NorthPolarStereo(central_longitude=0),
        colorbar=False
    )
    * mosaic_track.hvplot.points(
        "Longitude", "Latitude", color="Speed", label="Position / Speed",
        geo=True, projection=crs.NorthPolarStereo(central_longitude=0)
    )
    * gf.land * gf.coastline
).opts(height=600)

:Overlay
   .Feature.I                  :Feature   [Longitude,Latitude]
   .Polygons.I                 :Polygons   [nav_lon,nav_lat]   (iicethic)
   .Polygons.II                :Polygons   [nav_lon,nav_lat]   (iicethic)
   .Polygons.III               :Polygons   [nav_lon,nav_lat]   (iicethic)
   .Points.Position_over_Speed :Points   [Longitude,Latitude]   (Speed)
   .Land.I                     :Feature   [Longitude,Latitude]
   .Coastline.I                :Feature   [Longitude,Latitude]

_**FIXME:** How to turn off hovering? It's killing my CPU ..._

## Extract model data along ship track (all depths)

In [21]:
positions = list(zip(
    mosaic_track["Latitude"],
    mosaic_track["Longitude"],
))

lat_ind, lon_ind = xll2ij.get_ij(
    model_meshmask, positions, 't', xgcm=False, xarray_out=True)
lat_ind = lat_ind.rename({"location": "Date/Time"})
lon_ind = lon_ind.rename({"location": "Date/Time"})

In [22]:
len(lon_ind)

11919

In [23]:
%%time

model_dataset.coords["y"] = np.arange(model_dataset.dims["y"])
model_dataset.coords["x"] = np.arange(model_dataset.dims["x"])
model_dataset = model_dataset.compute()

# select
ship_track_data = model_dataset.sel(
    y=lat_ind, x=lon_ind, method="nearest"
)
ship_track_data.coords["Date/Time"] = mosaic_track.index

display(ship_track_data)

<xarray.Dataset>
Dimensions:               (Date/Time: 11919, axis_nbounds: 2, time_counter: 12)
Coordinates:
    nav_lat               (Date/Time) float32 69.70052 69.70052 ... 86.619514
    nav_lon               (Date/Time) float32 19.11818 19.11818 ... 119.202805
    time_centered         (time_counter) datetime64[ns] 2011-01-16T12:00:00 ... 2011-12-16T12:00:00
  * time_counter          (time_counter) datetime64[ns] 2011-01-16T12:00:00 ... 2011-12-16T12:00:00
    y                     (Date/Time) int64 442 442 442 442 ... 498 498 498 498
    x                     (Date/Time) int64 582 582 582 582 ... 180 180 180 180
  * Date/Time             (Date/Time) datetime64[ns] 2019-09-20T17:50:00 ... 2019-12-13T09:04:00
Dimensions without coordinates: axis_nbounds
Data variables:
    ice_pres              (time_counter, Date/Time) float32 0.0 0.0 ... 1.0 1.0
    time_centered_bounds  (time_counter, axis_nbounds) datetime64[ns] 2011-01-01 ... 2012-01-01
    time_counter_bounds   (time_counter, axis_nbounds) datetime64[ns] 2011-01-01 ... 2012-01-01
    ileadfra              (time_counter, Date/Time) float32 0.0 ... 0.9938303
    isnowthi              (time_counter, Date/Time) float32 0.0 ... 0.12785304
    iicethic              (time_counter, Date/Time) float32 0.0 0.0 ... 2.250129
    iiceprod              (time_counter, Date/Time) float32 0.0 ... 7.298921e-08
    iicetemp              (time_counter, Date/Time) float32 -0.0 ... -28.44586
    ioceflxb              (time_counter, Date/Time) float32 nan nan ... nan nan
    iicevelu              (time_counter, Date/Time) float32 0.0 ... 0.034964625
    iicevelv              (time_counter, Date/Time) float32 0.0 ... 0.036667008
    iicestru              (time_counter, Date/Time) float32 0.0 ... 0.035959244
    iicestrv              (time_counter, Date/Time) float32 0.0 ... 0.0077181812
    iicesflx              (time_counter, Date/Time) float32 0.0 0.0 ... 0.0 0.0
    iicenflx              (time_counter, Date/Time) float64 0.0 0.0 ... -1.324
    isnowpre              (time_counter, Date/Time) float32 4.2987933e-05 ... 3.013027e-06
Attributes:
    name:         FOCI1.14-JH024_1m_20110101_20111231
    description:  ice variables
    title:        ice variables
    Conventions:  CF-1.5
    production:   An IPSL model
    timeStamp:    2019-Apr-17 18:02:10 CEST
    history:      Wed Apr 17 18:48:52 2019: ncks -7 -a -L 1 --cnk_dmn time,1 ...
    NCO:          4.4.8

CPU times: user 278 ms, sys: 209 ms, total: 487 ms
Wall time: 1.72 s


In [24]:
(
    ship_track_data.isel(time_counter=11).iicethic.to_pandas().hvplot.line(label="Modeled december ice thickness")
    + mosaic_track["Speed"].hvplot.line(label="Polarstern Speed")
).cols(1)

:Layout
   .Curve.Modeled_december_ice_thickness :Curve   [Date/Time]   (0)
   .Curve.Polarstern_Speed               :Curve   [Date/Time]   (Speed)